# Lab 3.2: Creando un _Prompt Template_ para un modelo externo

En esta sección del laboratorio, crearás un _Detached Prompt Template_ que haga referencia a un modelo de IA generativa en **Azure OpenAI** para comenzar a gobernar este modelo en **watson<span style="color:#0066FF">x</span>.governance**. Aprenderás cómo realizar inferencias en este modelo externo utilizando el SDK de _Python_ de _OpenAI_.

### Prerrequisitos
* Credenciales de acceso a Azure OpenAI
* Credenciales de acceso a <b>watson<span style="color:#0066FF">x</span>.ai</b>
* Project ID

### Índice
1. Preparación
    - Librerías
    - Credenciales
2. Construcción del prompt
    - Redacción
    - Evaluación
3. Creación del _Detached Prompt Template_
    - Conexión a cliente de watsonx.ai
    - Creación del activo
4. Conclusión

## 1. Preparación

### Librerías

In [ ]:
! pip install --upgrade ibm-aigov-facts-client --no-cache
! pip install --upgrade openai azure-identity --no-cache
! pip install --upgrade rich --no-cache

In [ ]:
from ibm_aigov_facts_client import AIGovFactsClient, CloudPakforDataConfig, DetachedPromptTemplate, PromptTemplate
from ibm_aigov_facts_client.utils.enums import Task

from azure.identity import ClientSecretCredential, get_bearer_token_provider
from openai import AsyncAzureOpenAI

from IPython.display import display, Markdown
from rich import print

import pandas as pd

import asyncio
import os

### Credenciales

In [3]:
CPD_URL = "<EDIT>"
CPD_USERNAME = "<EDIT>"
CPD_APIKEY = "<EDIT>"

AZURE_OPENAI_ENDPOINT = "<EDIT>"
AZURE_OPENAI_DEPLOYMENT_NAME = "<EDIT>"
AZURE_CLIENT_ID = "<EDIT>"
AZURE_CLIENT_SECRET = "<EDIT>"
AZURE_TENANT_ID = "<EDIT>"

PROJECT_ID = os.getenv("PROJECT_ID", "<EDIT>")

## 2. Creación del Prompt

### Redacción

In [5]:
PROMPT_TEMPLATE = """
You will be given a ticket, and its department label. Please provide a numbered list of suggestions in spanish for actions to be performed by the agent assigned to this ticket. 

--- start of label ---
{label}
--- end of label ---

--- start of ticket ---
{ticket}
--- end of ticket ---
""".strip()

### Evaluación

In [6]:
def get_azure_token_provider():
    default_scope = "https://cognitiveservices.azure.com/.default"
    credential = ClientSecretCredential(
        tenant_id = os.environ.get('AZURE_TENANT_ID', AZURE_TENANT_ID),
        client_id = os.environ.get('AZURE_CLIENT_ID' ,AZURE_CLIENT_ID),
        client_secret = os.environ.get('AZURE_CLIENT_SECRET', AZURE_CLIENT_SECRET)
    )
    return get_bearer_token_provider(credential, default_scope)

async def summarize_resume(ticket:str, label:str, max_tokens:int=200, token_provider = None):
    if token_provider is None:
        token_provider = get_azure_token_provider()
    client = AsyncAzureOpenAI(
        azure_endpoint = os.environ.get('AZURE_OPENAI_ENDPOINT', AZURE_OPENAI_ENDPOINT),
        api_version = "2024-02-15-preview",
        azure_ad_token_provider = token_provider
    )
    model_response = await client.chat.completions.create(
        model = os.environ.get('AZURE_OPENAI_DEPLOYMENT_NAME', AZURE_OPENAI_DEPLOYMENT_NAME),
        messages = [{"role": "user", "content": PROMPT_TEMPLATE.format(ticket = ticket, label = label)}],
        max_tokens = max_tokens
    )
    return model_response.choices[0].message.content

async def summarize_batch(tickets:list, labels:list) -> list:
    token_provider = get_azure_token_provider()
    summaries = await asyncio.gather(
        *[summarize_resume(ticket, label, token_provider=token_provider) for ticket, label in zip(tickets, labels)]
    )
    return summaries

In [ ]:
data = pd.read_csv("https://raw.githubusercontent.com/maialenespi/TEL-content/main/evaluation-tickets.csv").head(10)
data

In [ ]:
data['generated_text'] = await summarize_batch(data['ticket'].values, data['label'].values)
data.head()

In [ ]:
def display_result(row):
    print(f"[bold]Ticket:[/bold]\n{row.ticket}\n\n[bold]Recomendaciones:[/bold]\n{row.generated_text}")

display_result(data.sample().iloc[0])

## 3. Creación de _Detached Prompt Template_

### Conexión a watsonx.ai

In [15]:
creds = CloudPakforDataConfig(
    service_url = CPD_URL,
    username = CPD_USERNAME,
    api_key = CPD_APIKEY
)

facts_client = AIGovFactsClient(
    cloud_pak_for_data_configs = creds,
    container_id = PROJECT_ID,
    container_type = "project",
    disable_tracing = True
)

### Creación de activo

In [16]:
model_information = DetachedPromptTemplate(
    prompt_id = "detached-openai-prompt",
    model_id = f"azure/{AZURE_OPENAI_DEPLOYMENT_NAME}",
    model_provider = "Azure OpenAI",
    model_name = "GPT-3.5-turbo",
    model_url = AZURE_OPENAI_ENDPOINT,
    prompt_url = "prompt_url",
    prompt_additional_info = {"model_owner": "Microsoft", "model_version": "gpt-3.5-turbo-1106"}
)

prompt_name = "Generación respuesta tickets - Detached Prompt (Azure OpenAI)"
prompt_description = "Un Detached Prompt para generación con Azure OpenAI"

prompt_template = PromptTemplate(
    input = PROMPT_TEMPLATE,
    prompt_variables = {"ticket": "", "label": ""},
)

In [ ]:
prompt_details = facts_client.assets.create_detached_prompt(
    model_id = f"azure/{AZURE_OPENAI_DEPLOYMENT_NAME}",
    task_id = Task.GENERATION,
    name = prompt_name,
    description = prompt_description,
    prompt_details = prompt_template,
    detached_information = model_information
)

project_prompt_id = prompt_details.to_dict()["asset_id"]

## 4. Conclusión

In [ ]:
factsheets_url = f"{CPD_URL}/wx/prompt-details/{project_prompt_id}/factsheet?context=wx&project_id={PROJECT_ID}"
display(Markdown(f"[Pulsa aquí para ver la AI Factsheet publicada]({factsheets_url})"))